# Pre-requisites for Amsterdam UMC DB


In [ ]:
# sets *your* project id
PROJECT_ID = "esicmdatathon2024" #@param {type:"string"}


In [ ]:
# sets default dataset for AmsterdamUMCdb
DATASET_PROJECT_ID = 'amsterdamumcdb' #@param {type:"string"}
DATASET_ID = 'version1_5_0' #@param {type:"string"}
LOCATION = 'eu' #@param {type:"string"}

In [ ]:
import os
from google.colab import auth

# all libraries check this environment variable, so set it:
os.environ["GOOGLE_CLOUD_PROJECT"] = PROJECT_ID

auth.authenticate_user()
print('Authenticated')


Authenticated


In [ ]:
%load_ext google.colab.data_table
from google.colab.data_table import DataTable

# change default limits:
DataTable.max_columns = 50
DataTable.max_rows = 30000


In [ ]:
from google.cloud.bigquery import magics
from google.cloud import bigquery

# sets the default query job configuration
def_config = bigquery.job.QueryJobConfig(default_dataset=DATASET_PROJECT_ID + "." + DATASET_ID)
magics.context.default_query_job_config = def_config


In [ ]:
import pandas as pd
import numpy as np

import matplotlib as plt
import seaborn as sns
sns.set_style('darkgrid')

# Get all the data together

## Part 1/2 get AKI patients

In [ ]:
%%bigquery AKI --project $PROJECT_ID
-- Combined SQL query to filter data initially and load into Pandas
WITH included_patients AS (
  SELECT person_id, visit_occurrence_id
  FROM visit_occurrence
  WHERE DATE_DIFF(visit_end_datetime, visit_start_datetime, hour)/24.0 >= 2
),
-- count measurements of creatinine > 1
patients_with_creatinine AS (
  SELECT person_id, visit_occurrence_id
  FROM measurement
  WHERE measurement_concept_id = 3020564 -- Creatinine
    AND provider_id IS NOT NULL
    AND visit_occurrence_id IN (
        SELECT visit_occurrence_id FROM included_patients
    )
  GROUP BY person_id, visit_occurrence_id
  HAVING COUNT(measurement_id) > 1
),
-- creatinine value > 400 before first visit
excluded_high_creatinine AS (
  SELECT DISTINCT visit_occurrence_id
  FROM measurement
  WHERE measurement_concept_id = 3020564 -- Creatinine
    AND provider_id IS NOT NULL
    AND measurement_datetime < (SELECT MIN(visit_start_datetime)
                            FROM visit_occurrence
                            WHERE visit_occurrence_id = measurement.visit_occurrence_id)
    AND value_as_number > 400
),
-- Exclude kidney transplant persons regardless of timestamp of procedure
excluded_nephrectomy_kidney_transplant AS (
  SELECT DISTINCT visit_occurrence_id
  FROM procedure_occurrence
  WHERE procedure_concept_id IN (4146256, 4021108, 4022014, 4322471) -- Nephrectomy and Kidney Transplant
  AND provider_id IS NOT NULL
),
-- Exclude rrt before first admission by person, not by visit
excluded_rrt_before_admission AS (
  SELECT DISTINCT p.visit_occurrence_id
  FROM procedure_occurrence p
  inner join visit_occurrence v
  on v.visit_occurrence_id = p.visit_occurrence_id
  WHERE p.procedure_concept_id = 4051330 -- RRT
    AND p.provider_id IS NOT NULL
    AND p.procedure_datetime < visit_start_datetime
),
-- exclude too little count of creatinine before the first RRT by person not by visit
excluded_few_creatinine_before_rrt AS (
  SELECT visit_occurrence_id
  FROM (
      SELECT visit_occurrence_id, COUNT(measurement_id) AS creatinine_measurement_count
      FROM measurement m
      WHERE measurement_concept_id = 3020564 --Creatinine
        AND provider_id IS NOT NULL
        AND measurement_datetime < (SELECT MIN(procedure_datetime)
                                FROM procedure_occurrence p
                                WHERE procedure_concept_id = 4051330 -- RRT
                                  AND provider_id IS NOT NULL
                                  AND p.visit_occurrence_id = m.visit_occurrence_id)
      GROUP BY m.visit_occurrence_id
  ) AS subquery
  WHERE creatinine_measurement_count <= 1
),

-- this gives the set of included persons
final_patients AS (
  SELECT person_id, visit_occurrence_id
  FROM patients_with_creatinine
  WHERE visit_occurrence_id NOT IN (SELECT visit_occurrence_id FROM excluded_high_creatinine)
    AND visit_occurrence_id NOT IN (SELECT visit_occurrence_id FROM excluded_nephrectomy_kidney_transplant)
    AND visit_occurrence_id NOT IN (SELECT visit_occurrence_id FROM excluded_rrt_before_admission)
    AND visit_occurrence_id NOT IN (SELECT visit_occurrence_id FROM excluded_few_creatinine_before_rrt)
),

first_scr AS (
  SELECT
    m.person_id
    , m.visit_occurrence_id
    , m.value_as_number AS first_scr
  FROM
    measurement m
  JOIN
    visit_occurrence v ON m.visit_occurrence_id = v.visit_occurrence_id
  WHERE
    m.measurement_concept_id = 3020564 -- Creatinine
    AND m.provider_id IS NOT NULL
    AND m.measurement_datetime BETWEEN timestamp_add(v.visit_start_datetime, INTERVAL -365 day)
                               AND timestamp_add(v.visit_start_datetime, INTERVAL 7 day)
    AND m.visit_occurrence_id IN (SELECT visit_occurrence_id FROM final_patients)
  QUALIFY
    ROW_NUMBER() OVER (PARTITION BY m.person_id, m.visit_occurrence_id
          -- this is to find the baseline scr nearest to the visit start datetime :
           ORDER BY abs(timestamp_diff(m.measurement_datetime, visit_start_datetime, minute)) asc ) = 1
),

aki_patients AS (
  SELECT
    m.visit_occurrence_id,
    max(m.value_as_number) AS highest_scr,
    max( case
        when m.value_as_number >= l.first_scr * 3.0 OR (m.value_as_number - l.first_scr) >= 353.6
         then 3
         when  (m.value_as_number >= l.first_scr * 2.0 AND m.value_as_number < l.first_scr * 3.0)
         then 2
        when (m.value_as_number >= l.first_scr * 1.5 AND m.value_as_number < l.first_scr * 2.0) OR
        (m.value_as_number - l.first_scr) >= 26.5
         then 1
        end
    ) as scr_aki
  FROM
    measurement m
  JOIN
    first_scr l ON m.visit_occurrence_id = l.visit_occurrence_id
  WHERE
    m.measurement_concept_id = 3020564 -- creatinine
    AND m.provider_id IS NOT NULL
    AND m.measurement_date > (SELECT MIN(visit_start_date) FROM visit_occurrence WHERE visit_occurrence_id = m.visit_occurrence_id)
    AND (
        (m.value_as_number >= l.first_scr * 1.5 AND m.value_as_number < l.first_scr * 2.0) OR
        (m.value_as_number - l.first_scr) >= 26.5 OR
        (m.value_as_number >= l.first_scr * 2.0 AND m.value_as_number < l.first_scr * 3.0) OR
        m.value_as_number >= l.first_scr * 3.0 OR
        (m.value_as_number - l.first_scr) >= 353.6
    )
    AND m.visit_occurrence_id IN (SELECT visit_occurrence_id FROM final_patients)
  group by m.visit_occurrence_id, l.first_scr
),

-- finds RRT procedures after admission
rrt_initiation AS (
  SELECT
    p.person_id,
    p.visit_occurrence_id,
    min(p.procedure_datetime) as procedure_datetime,
    -- time from admission to start of RRT procedure
    date_diff( min(p.procedure_datetime), v.visit_start_datetime, minute)/60.0 as admit_to_rrt_hours
  FROM
    procedure_occurrence p
    inner join visit_occurrence v on p.visit_occurrence_id = v.visit_occurrence_id
  WHERE
    procedure_concept_id IN (4051330) -- RRT procedures
    AND procedure_datetime >= visit_start_datetime
    AND p.visit_occurrence_id IN (SELECT visit_occurrence_id FROM final_patients)
    AND p.provider_id IS NOT NULL
  group by person_id, visit_occurrence_id, visit_start_datetime
)

SELECT
  fp.person_id,
  fp.visit_occurrence_id,
  fs.first_scr,
  ak.highest_scr, ak.scr_aki,
  rrt.procedure_datetime AS rrt_start_date
FROM
  final_patients fp
left join
  first_scr fs on fp.visit_occurrence_id = fs.visit_occurrence_id
LEFT JOIN
  aki_patients ak ON fp.visit_occurrence_id = ak.visit_occurrence_id
LEFT JOIN
  rrt_initiation rrt ON fp.visit_occurrence_id = rrt.visit_occurrence_id;


Query is running:   0%|          |

Downloading:   0%|          |

In [ ]:
s = AKI.select_dtypes(include='object').columns
AKI[s] = AKI[s].astype("float")


In [ ]:
AKI.describe()

person_id  visit_occurrence_id    first_scr  highest_scr   scr_aki
count        7908.0               7908.0  7899.000000  2195.000000    2195.0
mean   10191.585989         11804.347876   103.329662   239.400000  1.489749
std     5842.813298          6773.250533    67.085880   137.652305  0.715284
min             4.0                  4.0     4.000000    10.000000       1.0
25%         5163.25               5960.0    67.000000   147.000000       1.0
50%         10215.5              11837.5    88.000000   208.000000       1.0
75%        15233.25             17642.75   117.000000   300.500000       2.0
max         20322.0              23548.0  2157.000000  3187.000000       3.0

## Part 2/2 Urine output per weight



### Weight and urine output


In [ ]:
%%bigquery urine_roll_avg --project $PROJECT_ID
with bd_wght as (
SELECT m.visit_occurrence_id, m.value_as_number as body_weight
  FROM measurement m
  WHERE measurement_concept_id in (3026600, 3013762, 3023166, 3025315) -- Body Weight
    AND m.provider_id IS NULL
) ,
-- using the heart rate to determine if a person is at the bedside, gets all hours of stay of a person
-- use "distinct" to remove duplicate entries
hr_hours as (
  select distinct m.person_id, m.visit_occurrence_id,  DATETIME_TRUNC(measurement_datetime, HOUR) rounded_to_hour
  from visit_occurrence v
  inner join measurement m  on m.visit_occurrence_id = v.visit_occurrence_id
  where m.provider_id is not null
    and m.measurement_concept_id = 21490872 -- Heart rate.beat-to-beat by EKG
    and date_diff(v.visit_end_datetime, v.visit_start_datetime, hour)/24.0 >= 2
    and m.measurement_datetime between v.visit_start_datetime
              and timestamp_add (visit_start_datetime, Interval 7*24 hour)
  -- and m.person_id = 12  -- random test
),
-- get all urine output charted. round the measurement time to the nearest hour
-- use "distinct" to remove duplicate entries
urine_hours as (
  select distinct m.person_id, m.visit_occurrence_id, m.value_as_number , m.measurement_datetime
    , DATETIME_TRUNC(measurement_datetime, HOUR) rounded_to_hour
  from measurement m
  inner join visit_occurrence v
  on m.visit_occurrence_id = v.visit_occurrence_id
  and date_diff(v.visit_end_datetime, v.visit_start_datetime, hour)/24.0 >= 2
  where m.measurement_concept_id in (3014315, 3016267, 21491173, 3007123) -- Urine
    and m.provider_id is not null
    and m.measurement_datetime between v.visit_start_datetime and timestamp_add (visit_start_datetime, Interval 7*24 hour)
    and m.value_as_number > 1 -- to avoid possible entries of 0 for "UrineIncontinentie"
  --  and m.person_id = 12 -- test only, random
) ,
-- fill all rows where there is a heart rate but no urine output as zero urine for the hour
urine_fillnull as(
select h.*, ifnull(u.value_as_number,0) as urine_hour
from hr_hours h left outer join urine_hours u
on h.visit_occurrence_id = u.visit_occurrence_id
and h.rounded_to_hour = u.rounded_to_hour
),
-- calculate 6 hour and 12 hour rolling averages
roll_avg as (
select person_id, visit_occurrence_id, rounded_to_hour
, avg(urine_hour) over(partition by visit_occurrence_id order by rounded_to_hour rows between 24 preceding and current row) as avg_24_roll_urine
, avg(urine_hour) over(partition by visit_occurrence_id order by rounded_to_hour rows between 12 preceding and current row) as avg_12_roll_urine
, avg(urine_hour) over(partition by visit_occurrence_id order by rounded_to_hour rows between 6 preceding and current row) as avg_6_roll_urine
from urine_fillnull
)
select a.person_id, a.visit_occurrence_id, w.body_weight
, avg(avg_24_roll_urine/w.body_weight) AS rolling_mean_24h_mL_kg_h
, avg(avg_12_roll_urine/w.body_weight) AS rolling_mean_12h_mL_kg_h
, avg(avg_6_roll_urine/w.body_weight) AS rolling_mean_6h_mL_kg_h
from roll_avg a inner join bd_wght w
on a.visit_occurrence_id = w.visit_occurrence_id
group by a.person_id, a.visit_occurrence_id, w.body_weight


Query is running:   0%|          |

Downloading:   0%|          |

In [ ]:
s = urine_roll_avg.select_dtypes(include='object').columns
urine_roll_avg[s] = urine_roll_avg[s].astype("float")

urine_roll_avg


person_id  visit_occurrence_id  body_weight  \
0          2461                 2851        105.0   
1          7605                 8819        105.0   
2         16302                18902        105.0   
3         17657                20451        105.0   
4          7719                 8948        105.0   
...         ...                  ...          ...   
7997       1541                 1775         95.0   
7998       9204                10670         95.0   
7999      17696                20493         95.0   
8000       5309                 6128         95.0   
8001       5823                 6744         95.0   

      urine_output_per_kg_avg_roll24hr  urine_output_per_kg_avg_roll12hr  \
0                             0.433363                          0.517848   
1                             0.222739                          0.180480   
2                             1.161110                          1.220127   
3                             2.395985                          2.551932   
4                             0.631486                          0.621141   
...                                ...                               ...   
7997                          2.253703                          2.375686   
7998                          1.308182                          1.360931   
7999                          0.931094                          1.062011   
8000                          0.787085                          0.755882   
8001                          1.968499                          1.964981   

      urine_output_per_kg_avg_roll6hr  
0                            0.536120  
1                            0.144107  
2                            1.260212  
3                            2.633256  
4                            0.608867  
...                               ...  
7997                         2.435167  
7998                         1.387885  
7999                         1.124459  
8000                         0.730596  
8001                         1.991479  

[8002 rows x 6 columns]

## merge AKI with Urine output

In [ ]:
cols_to_use = urine_roll_avg.columns.difference(AKI.columns)
cols_to_use = cols_to_use.insert( 0,'visit_occurrence_id')
df = pd.merge(AKI, urine_roll_avg[cols_to_use], how='left', left_on='visit_occurrence_id', right_on='visit_occurrence_id')


Clean up to save space

In [ ]:
del AKI, urine_roll_avg

In [ ]:
s = df.select_dtypes(include='object').columns
df[s] = df[s].astype("float")

df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 7908 entries, 0 to 7907
Data columns (total 10 columns):
 #   Column                    Non-Null Count  Dtype              
---  ------                    --------------  -----              
 0   person_id                 7908 non-null   Int64              
 1   visit_occurrence_id       7908 non-null   Int64              
 2   first_scr                 7899 non-null   float64            
 3   highest_scr               2195 non-null   float64            
 4   scr_aki                   2195 non-null   Int64              
 5   rrt_start_date            693 non-null    datetime64[us, UTC]
 6   body_weight               7666 non-null   float64            
 7   rolling_mean_12h_mL_kg_h  7666 non-null   float64            
 8   rolling_mean_24h_mL_kg_h  7666 non-null   float64            
 9   rolling_mean_6h_mL_kg_h   7666 non-null   float64            
dtypes: Int64(3), datetime64[us, UTC](1), float64(6)
memory usage: 641.1 KB


## Extra conditions for KDIGO

In [ ]:

condition_1_mask = (
    (df['rolling_mean_12h_mL_kg_h'] == 0) |
    (df['rolling_mean_24h_mL_kg_h'] < 0.3) |
    (df['highest_scr'] >= df['first_scr'] * 3.0) |
    ((df['highest_scr'] - df['first_scr']) >= 353.6) |
    (df['rrt_start_date'].notnull())
)

condition_2_mask = (
    ~condition_1_mask & (
        ((df['highest_scr'] >= df['first_scr'] * 2.0) & (df['highest_scr'] < df['first_scr'] * 3.0)) |
        (df['rolling_mean_12h_mL_kg_h'] < 0.5)
    )
)

condition_3_mask = (
    ~condition_1_mask & ~condition_2_mask & (
        (df['rolling_mean_6h_mL_kg_h'] < 0.5) |
        ((df['highest_scr'] >= df['first_scr'] * 1.5) & (df['highest_scr'] < df['first_scr'] * 2.0)) |
        ((df['highest_scr'] - df['first_scr']) >= 26.5)
    )
)

df['worst_KDIGO'] = np.select(
    [condition_1_mask, condition_2_mask, condition_3_mask],
    [3, 2, 1],
    default=0
)


# Other parameters for clustering

## demographics


In [ ]:
%%bigquery demographics_df --project $PROJECT_ID
WITH Demographics AS (
    SELECT
        vo.person_id,
        vo.visit_occurrence_id,
        EXTRACT(YEAR FROM CURRENT_DATE) - p.year_of_birth AS age,
        CASE WHEN p.gender_concept_id = 8507 THEN 'Male'
             WHEN p.gender_concept_id = 8532 THEN 'Female'
             ELSE 'Other'
             END AS sex
    FROM
        visit_occurrence vo
    LEFT JOIN
        person p ON vo.person_id = p.person_id
),

HeightMeasurements AS (
    SELECT
        m.person_id,
        CAST(AVG(m.value_as_number) AS FLOAT64) AS avg_height
    FROM
        measurement m
    WHERE
        m.measurement_concept_id IN (3035463, 3023540, 3019171, 3036277) -- height
        AND provider_id IS NULL
        AND m.visit_occurrence_id IS NOT NULL  -- Ensure measurement is linked to a visit
    GROUP BY
        m.person_id
),

WeightMeasurements AS (
    SELECT
        m.person_id,
        CAST(AVG(m.value_as_number) AS FLOAT64) AS avg_weight
    FROM
        measurement m
    WHERE
        m.measurement_concept_id IN (3026600, 3013762, 3023166, 3025315) -- weight
        AND provider_id IS NULL
        AND m.visit_occurrence_id IS NOT NULL  -- Ensure measurement is linked to a visit
    GROUP BY
        m.person_id
)

SELECT
    d.person_id,
    d.visit_occurrence_id,
    d.age,
    d.sex,
    h.avg_height AS height,
    w.avg_weight AS weight,
    CAST(w.avg_weight / (h.avg_height / 100) / (h.avg_height / 100) AS FLOAT64) AS bmi
FROM
    Demographics d
LEFT JOIN
    HeightMeasurements h ON d.person_id = h.person_id
LEFT JOIN
    WeightMeasurements w ON d.person_id = w.person_id


Query is running:   0%|          |

Downloading:   0%|          |

## Reason for admission

In [ ]:
%%bigquery reasons_df --project $PROJECT_ID
SELECT
  visit_occurrence_id,
  value_as_string AS reasons_for_admission
FROM
  observation
WHERE
  observation_concept_id = 37154585
  AND provider_id IS NOT NULL



Query is running:   0%|          |

Downloading:   0%|          |

In [ ]:
reasons_df.describe()

visit_occurrence_id
count             107343.0
mean          11447.168898
std            6792.697931
min                    0.0
25%                 5555.0
50%                11253.0
75%                17431.0
max                23552.0

In [ ]:
reasons_df['visit_occurrence_id'].nunique()

10317

## Reasons, conditions, procedures